In [2]:
import torch
from transformers import Qwen2_5_VLForConditionalGeneration, AutoTokenizer, AutoProcessor
# from qwen_vl_utils import process_vision_info
from PIL import Image
import os
import numpy as np
from tqdm import tqdm

# --- Configuration ---
MODEL_NAME = "Qwen/Qwen2.5-VL-3B-Instruct"  # You can choose other model sizes

IMAGE_DIR = "/home/nguyendc/model-factory/Finetuning-Automation/etc/data/media/docai_mgp_facture_v2_0/"
BATCH_SIZE = 4
# --- End Configuration ---

# Check for GPU availability
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using device: {device}")

# Load the model and processor
model = Qwen2_5_VLForConditionalGeneration.from_pretrained(
    MODEL_NAME, torch_dtype="bfloat16", device_map="cuda", attn_implementation="flash_attention_2",
)
processor = AutoProcessor.from_pretrained(MODEL_NAME, trust_remote_code=True)

2025-09-02 15:00:12.976185: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1756825212.987686 3903757 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1756825212.991038 3903757 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1756825213.000855 3903757 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1756825213.000880 3903757 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1756825213.000882 3903757 computation_placer.cc:177] computation placer alr

[2025-09-02 15:00:17,970] [INFO] [real_accelerator.py:222:get_accelerator] Setting ds_accelerator to cuda (auto detect)


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status
/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


Using device: cuda


Loading checkpoint shards: 100%|██████████| 2/2 [00:01<00:00,  1.09it/s]
Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


In [2]:
processor

Qwen2_5_VLProcessor:
- image_processor: Qwen2VLImageProcessor {
  "do_convert_rgb": true,
  "do_normalize": true,
  "do_rescale": true,
  "do_resize": true,
  "image_mean": [
    0.48145466,
    0.4578275,
    0.40821073
  ],
  "image_processor_type": "Qwen2VLImageProcessor",
  "image_std": [
    0.26862954,
    0.26130258,
    0.27577711
  ],
  "max_pixels": 12845056,
  "merge_size": 2,
  "min_pixels": 3136,
  "patch_size": 14,
  "processor_class": "Qwen2_5_VLProcessor",
  "resample": 3,
  "rescale_factor": 0.00392156862745098,
  "size": {
    "longest_edge": 12845056,
    "shortest_edge": 3136
  },
  "temporal_patch_size": 2
}

- tokenizer: Qwen2TokenizerFast(name_or_path='Qwen/Qwen2.5-VL-3B-Instruct', vocab_size=151643, model_max_length=131072, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'eos_token': '<|im_end|>', 'pad_token': '<|endoftext|>', 'additional_special_tokens': ['<|im_start|>', '<|im_end|>', '<|object_ref_start|>', '<|object_ref_end|>', '<

In [ ]:
def get_image_embeddings(image_paths):
    """
    Processes a batch of images and extracts their embeddings.
    """
    images_pil = []
    valid_paths = []
    for path in image_paths:
        if path.lower().endswith(('.png', '.jpg', '.jpeg')):
            try:
                # The processor expects PIL images in RGB format
                images_pil.append(Image.open(path).convert("RGB"))
                valid_paths.append(path)
            except Exception as e:
                print(f"Warning: Could not load image {path}. Skipping. Error: {e}")

    if not images_pil:
        return np.array([]), []

    # For pure vision feature extraction, we can provide an empty text prompt.
    # The processor handles tokenizing text and preparing images.
    inputs = processor(
        text=[""] * len(images_pil),
        images=images_pil,
        padding=True,
        return_tensors="pt"
    ).to(device)

    with torch.no_grad():
        # Get the vision embeddings from the model's vision tower
        vision_outputs = model.visual(inputs['pixel_values'].to(dtype=model.dtype), grid_thw=inputs['image_grid_thw'])
        # We'll use the pooled output as the embedding
        embeddings = vision_outputs

    return embeddings.to(torch.float16).cpu().numpy()

In [ ]:
import json

# --- Process all images in the directory ---
image_files = [os.path.join(IMAGE_DIR, f) for f in os.listdir(IMAGE_DIR) if f.lower().endswith(('.png', '.jpg', '.jpeg'))]
all_embeddings = []
filepaths = []

with open("embeddings_factures_osteopathie_1k_qwen.json", "w") as f:

    f.write("[\n")
    first = True
    for i in tqdm(range(0, len(image_files), BATCH_SIZE)):
        batch_paths = image_files[i:i+BATCH_SIZE]
        batch_embeddings = get_image_embeddings(batch_paths)
        embeddings_list = [emb.tolist() for emb in batch_embeddings]
        for path, emb in zip(batch_paths, embeddings_list):
            if not first:
                f.write(",\n")
            json.dump({"filepath": path, "embedding": emb}, f)
            first = False
    f.write("\n]\n")

print("Embeddings extracted and saved.")

100%|██████████| 700/700 [22:12<00:00,  1.90s/it]

Embeddings extracted and saved.


In [4]:
from sklearn.cluster import DBSCAN, MeanShift, AffinityPropagation
from sklearn.preprocessing import normalize
from sklearn.metrics import silhouette_score
from sklearn.neighbors import NearestNeighbors
from sklearn.decomposition import PCA
import argparse
import warnings
warnings.filterwarnings('ignore')
from sklearn.metrics.pairwise import cosine_similarity
from datetime import datetime
import json

embeddings_path = "/home/nguyendc/sonnh/embedding-clustering/extract/embeddings_factures_osteopathie_1k_qwen.json"
with open(embeddings_path, 'r') as f:
    data = json.load(f)

file_paths = []
embeddings_list = []

for item in data:
    file_paths.append(item['filepath'])
    embeddings_list.append(item['embedding'])

embeddings = np.array(embeddings_list, dtype=np.float32)
print(f"Loaded {len(file_paths)} samples with embedding dimension {embeddings.shape[1]}")

# Normalize embeddings using L2 normalization for cosine distance
embeddings_normalized = normalize(embeddings, norm='l2', axis=1)
print("Applied L2 normalization to embeddings")

sims = cosine_similarity(embeddings)
print(embeddings.shape)
# lấy upper triangle exclude diagonal để inspect
triu_idxs = np.triu_indices_from(sims, k=1)
dist_vals = sims[triu_idxs]
print(dist_vals.shape)
print("mean sim:", dist_vals.mean(), "std:", dist_vals.std())

Loaded 2800 samples with embedding dimension 2048
Applied L2 normalization to embeddings
(2800, 2048)
(3918600,)
mean sim: 0.37961555 std: 0.22605234


In [ ]:
import fiftyone as fo
import fiftyone.brain as fob
import numpy as np
from sklearn.mixture import GaussianMixture
import json

DATASET_NAME = "mock"

json_path = "./embeddings_factures_osteopathie_1k_qwen.json"

with open(json_path, "r") as file:
    embedding_data = json.load(file)

file_paths = []
embeddings = []
for i, record in enumerate(embedding_data):
    file_paths.append(record.get("filepath"))
    embeddings.append(record.get("embedding"))

if DATASET_NAME in fo.list_datasets():
    dataset = fo.load_dataset(DATASET_NAME)
    dataset.delete()
dataset = fo.Dataset(DATASET_NAME)

# Add samples to the dataset
samples = [fo.Sample(filepath=p) for p in file_paths]
dataset.add_samples(samples)

# Building Gaussian mixture model (GMM)
n_gaussians = 50
gmm = GaussianMixture(n_components=n_gaussians, random_state=42)
gmm.fit(embeddings)
cluster_labels = gmm.predict(embeddings)

# Adding labeled embeddings to visulization
dataset.add_sample_field("gmm_cluster", fo.IntField)
for sample, label in zip(dataset, cluster_labels):
    sample["gmm_cluster_50_gaussians"] = int(label)
    sample.save()

n_gaussians = 200
gmm = GaussianMixture(n_components=n_gaussians, random_state=42)
gmm.fit(embeddings)
cluster_labels = gmm.predict(embeddings)

# Adding labeled embeddings to visulization
dataset.add_sample_field("gmm_cluster", fo.IntField)
for sample, label in zip(dataset, cluster_labels):
    sample["gmm_cluster_200_gaussians"] = int(label)
    sample.save()

# --- Visualize the Embeddings with UMAP ---
# This will compute a 2D representation of your embeddings
# for visualization.
res = fob.compute_visualization(
    dataset,
    embeddings=embeddings,
    brain_key="qwen_vision_viz",
    method="tsne",
    verbose=True
)
dataset.set_values("qwen_umap", res.current_points)

print("UMAP visualization computed. Launch the app to see the plot.")
session = fo.launch_app(dataset)

 100% |███████████████| 1091/1091 [174.1ms elapsed, 0s remaining, 6.3K samples/s]   
